### Cell 1 – Install required libraries

This cell installs `segment-geospatial` and its extra dependencies.  
They include tools for the Segment Anything Model (SAM) and interactive maps, so you must run this once in every new Colab runtime.


In [ ]:
# Cell 1 – Install segment-geospatial + extras for Colab
# Make sure the Colab runtime uses a GPU: Runtime -> Change runtime type -> GPU

!pip install -q "segment-geospatial[extra]"


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.6/56.6 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.8/152.8 kB 8.9 MB/s eta 0:00:00


In [ ]:
!pip install leafmap

### Cell 2 – Import main Python packages

This cell imports the libraries we need for the interactive map and segmentation.  
`leafmap` handles the map and drawing tools, and `SamGeo` runs the pretrained SAM model.


In [ ]:
# Cell 2 – Imports

import os

import leafmap               # interactive map (built on ipyleaflet/folium)
from samgeo import SamGeo    # main SAMGeo class
from samgeo.common import tms_to_geotiff  # download tiles into a GeoTIFF

print("leafmap version:", leafmap.__version__)


leafmap version: 0.57.9


### Cell 3 – Create a map over the Turkey earthquake area

This cell creates an interactive satellite map centered over southern Türkiye.  
You can zoom, pan, and use the draw tools to select the area of interest (AOI) for segmentation.


In [ ]:
# Cell 3 – Create an interactive map centered near the Turkey–Syria earthquake area

import leafmap

# Create an interactive map over southern Türkiye
zoom = 17  # or 7–10 if you want a wider area
m = leafmap.Map(center=[37.575275, 36.922821], zoom=zoom)
m.add_basemap("SATELLITE")
m


Map(center=[37.575275, 36.922821], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

### Cell 4 – Read the AOI drawn on the map

This cell reads the bounding box of the shape you drew on the map.  
If you forget to draw an AOI, it uses a small default box in the earthquake region.


In [ ]:
# Cell 4 – Get the bounding box (min_lon, min_lat, max_lon, max_lat) from user-drawn AOI

bbox = m.user_roi_bounds()

if bbox is None:
    # Fallback: a small default box in the earthquake region (approximate)
    # Format: [min_lon, min_lat, max_lon, max_lat]
    bbox = [36.87, 37.55, 36.98, 37.60]
    print("No ROI drawn. Using default bounding box around SE Turkey:", bbox)
else:
    print("Using user-drawn bounding box:", bbox)


Using user-drawn bounding box: [36.9198, 37.5747, 36.9212, 37.5758]


### Cell 5 – Download satellite imagery for the AOI

This cell downloads satellite map tiles for the selected AOI and saves them as a GeoTIFF image.  
The GeoTIFF is the input image that the SAM model will later segment.


In [ ]:
# Cell 5 – Download map tiles into a GeoTIFF image

image_path = "turkey_eq_satellite.tif"

# zoom=19 or 20 gives very detailed imagery; you can lower it if GPU memory is tight.
tms_to_geotiff(
    output=image_path,
    bbox=bbox,
    zoom=19,
    source="Satellite",   # uses the 'SATELLITE' basemap source
    overwrite=True,
)

print("Downloaded image to:", image_path)


Downloaded image 1/9
Downloaded image 2/9
Downloaded image 3/9
Downloaded image 4/9
Downloaded image 5/9
Downloaded image 6/9
Downloaded image 7/9
Downloaded image 8/9
Downloaded image 9/9
Saving GeoTIFF. Please wait...
Image saved to turkey_eq_satellite.tif
Downloaded image to: turkey_eq_satellite.tif


### Cell 6 – Load the pretrained SAMGeo model

This cell initializes the SAMGeo object with a pretrained Segment Anything model (ViT-H).  
We do not train anything; we just load the ready model so it can segment the downloaded image.


In [ ]:
# Cell 6 – Initialize the SAMGeo model (pretrained Segment Anything)

sam = SamGeo(
    model_type="vit_h",                 # big model (best quality, heavier)
    checkpoint="sam_vit_h_4b8939.pth",  # checkpoint name used in SAMGeo examples
    sam_kwargs=None,
)

print("SAM model initialized.")


Model checkpoint for vit_h not found.


Downloading...
From: https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth
To: /root/.cache/torch/hub/checkpoints/sam_vit_h_4b8939.pth
100%|██████████| 2.56G/2.56G [00:14<00:00, 183MB/s]


SAM model initialized.


### Cell 7 – Run automatic segmentation on the image

This cell runs SAM on the GeoTIFF and creates a segmentation mask.  
Each region (segment) in the mask represents an object or area SAM detects in the satellite image.


In [ ]:
# Cell 7 – Segment the satellite image automatically

mask_path = "turkey_eq_segment.tif"

sam.generate(
    image_path,
    mask_path,
    batch=True,             # process in batches (useful for larger images)
    foreground=True,        # try to segment "things" in the image
    erosion_kernel=(3, 3),
    mask_multiplier=255,    # 0–255 mask (common in image tools)
)

print("Segmentation mask saved to:", mask_path)


100%|██████████| 4/4 [00:32<00:00,  8.09s/it]

Segmentation mask saved to: turkey_eq_segment.tif


### Cell 8 – Convert the mask to vector polygons

This cell converts the raster mask into vector polygons and saves them to a GeoPackage file.  
Vector polygons are easier to visualize, style, and export for GIS analysis.


In [ ]:
# Cell 8 – Polygonize mask to GeoPackage (vector format)

vector_path = "turkey_eq_segment.gpkg"

sam.tiff_to_gpkg(
    mask_path,
    vector_path,
    simplify_tolerance=None,   # you can set a value (e.g., 0.5) to simplify geometry
)

print("Vector polygons saved to:", vector_path)


Vector polygons saved to: turkey_eq_segment.gpkg


In [ ]:
# Optional – Save as Shapefile
shp_path = "turkey_eq_segment.shp"
sam.tiff_to_vector(mask_path, shp_path)
print("Shapefile saved to:", shp_path)


Shapefile saved to: turkey_eq_segment.shp


### Cell 9 – Visualize the segmentation on the map

This cell adds the downloaded GeoTIFF and the segmentation polygons back onto the interactive map.  
You can switch layers on and off and visually inspect how SAM segmented the earthquake area.


In [ ]:
# Cell 9 – Show the segmentation result on the map

# Turn off the original basemap (so the GeoTIFF is visible)
if len(m.layers) > 0:
    m.layers[-1].visible = False  # last layer is usually the basemap we added first

# Add the downloaded GeoTIFF as a raster layer
m.add_raster(image_path, layer_name="Satellite Image")

# Style for vector polygons
style = {
    "color": "#3388ff",
    "weight": 1,
    "fillColor": "#ff7800",
    "fillOpacity": 0.4,
}

m.add_vector(vector_path, layer_name="SAM Segments", style=style)

m


Map(bottom=12993299.0, center=[37.57525, 36.920500000000004], controls=(ZoomControl(options=['position', 'zoom…

### Cell 1 – Install required packages

This cell installs the Python libraries we need:

- **leafmap** – to search and download Maxar Open Data and work with maps.
- **geopandas / shapely** – to handle building polygons.
- **rasterio** – to read/write GeoTIFF images.
- **rasterstats** – used through `leafmap.zonal_stats` to summarize change per building.

Run this once when you open the notebook.


In [ ]:
!pip install -q leafmap geopandas rasterio rasterstats shapely


### Cell 2 – Imports and helper function

This cell:

- Imports the libraries.
- Defines a small helper `maxar_local_path` that reconstructs the **local file path** used by `leafmap.maxar_download` for each downloaded Maxar image. :contentReference[oaicite:1]{index=1}


In [ ]:
import os
import numpy as np
import geopandas as gpd
import rasterio
from rasterio.transform import Affine
from rasterio.warp import reproject, Resampling

import leafmap          # functions: maxar_search, zonal_stats, etc.
import leafmap.foliumap as leafmap_map  # for interactive maps

def maxar_local_path(url, out_dir="."):
    """
    Rebuild the local file path that leafmap.maxar_download() uses
    for a given Maxar 'visual' image URL.
    """
    items = url.split("/")
    file_name = items[7] + ".tif"
    dir_name = items[-1].split("-")[0]
    return os.path.join(out_dir, dir_name, file_name)


### Cell 3 – Select AOI and find pre/post-event Maxar images

This cell:

1. Sets the **Maxar collection ID** for the 2023 Turkey earthquake:
   `Kahramanmaras-turkey-earthquake-23`. :contentReference[oaicite:2]{index=2}  
2. Opens a map and shows footprints of **pre-event** (red) and **post-event** (blue) Maxar tiles.
3. Lets you draw a rectangle **AOI (area of interest)** on the map.
4. Uses the AOI bounding box to search for **pre** and **post** images that cover your AOI.

> After you run it:
> - Draw a rectangle on the map over the area you like.
> - Click the square stop button in the cell when you’re done drawing so the code can continue.


In [ ]:
# Cell 3 – Select event, get pre/post tiles, and show footprints on a map
# (fixed to avoid Timestamp JSON error)

collection = "Kahramanmaras-turkey-earthquake-23"

# Get pre- and post-event image footprints for the whole event
pre_gdf = leafmap.maxar_search(collection, end_date="2023-02-06")
post_gdf = leafmap.maxar_search(collection, start_date="2023-02-06")

print(f"Pre-event tiles: {len(pre_gdf)}, Post-event tiles: {len(post_gdf)}")

# 🔧 FIX: convert any datetime columns to string so they can be sent to the map as JSON
for gdf in (pre_gdf, post_gdf):
    datetime_cols = gdf.select_dtypes(include=["datetime64[ns]", "datetime64[ns, UTC]"]).columns
    for col in datetime_cols:
        gdf[col] = gdf[col].astype(str)

# Create the interactive map and add the footprints
m = leafmap_map.Map()        # or leafmap.Map() if you prefer
pre_style = {"color": "red", "fillColor": "red", "opacity": 1, "fillOpacity": 0.5}

m.add_gdf(pre_gdf, layer_name="Pre-event tiles", style=pre_style, info_mode="on_click")
m.add_gdf(post_gdf, layer_name="Post-event tiles", info_mode="on_click")
m.add_basemap("SATELLITE")

m


Pre-event tiles: 229, Post-event tiles: 1886


### Cell 4 – Capture AOI bounding box and pick one pre/post tile

This cell:

- Reads the bounding box of your drawn AOI (`[xmin, ymin, xmax, ymax]`).
- If you didn’t draw anything, it falls back to a default AOI near Kahramanmaraş.
- Searches again, but now only for tiles that intersect your AOI.
- Picks the **first** pre-event and post-event image for that AOI as a simple example.

You can later refine the logic to pick specific tiles if you want.


In [ ]:
# Get AOI bounding box from the map
bbox = m.user_roi_bounds()
if bbox is None:
    # Default AOI in the Kahramanmaraş region (you can change this)
    bbox = [36.9172, 37.5728, 36.9229, 37.5772]

print("AOI bounding box [xmin, ymin, xmax, ymax]:", bbox)

# Search for pre/post event images within the AOI
pre_event = leafmap.maxar_search(collection, bbox=bbox, end_date="2023-02-06")
post_event = leafmap.maxar_search(collection, bbox=bbox, start_date="2023-02-06")

print("Pre tiles in AOI:", len(pre_event))
print("Post tiles in AOI:", len(post_event))

if len(pre_event) == 0 or len(post_event) == 0:
    raise RuntimeError("No pre/post tiles found for this AOI. Try a different area or larger box.")

# For this simple demo, just take the first pre and first post tile
pre_images = pre_event["visual"].tolist()
post_images = post_event["visual"].tolist()

pre_url = pre_images[0]
post_url = post_images[0]

print("Using pre-event image:", pre_url)
print("Using post-event image:", post_url)


The folium plotting backend does not support this function.
AOI bounding box [xmin, ymin, xmax, ymax]: [36.9172, 37.5728, 36.9229, 37.5772]
Pre tiles in AOI: 1
Post tiles in AOI: 4
Using pre-event image: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2022-07-26/10300100D797E100-visual.tif
Using post-event image: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2023-02-08/10300500D9F8D200-visual.tif


### Cell 5 – Download the selected pre and post Maxar images

This cell:

- Downloads the pre and post **visual** GeoTIFF images using `leafmap.maxar_download`.
- Uses the same naming logic as `leafmap` to compute local file paths for the first pre and post images.

The download may take a bit, depending on your connection.


In [ ]:
out_dir = "maxar_tiles"
os.makedirs(out_dir, exist_ok=True)

# Download lists (pre and post sets)
leafmap.maxar_download(pre_images, out_dir=out_dir, quiet=False)
leafmap.maxar_download(post_images, out_dir=out_dir, quiet=False)

# Get local file paths for the first chosen pre/post images
pre_path = maxar_local_path(pre_url, out_dir=out_dir)
post_path = maxar_local_path(post_url, out_dir=out_dir)

print("Local pre-event path:", pre_path)
print("Local post-event path:", post_path)

if not (os.path.exists(pre_path) and os.path.exists(post_path)):
    raise FileNotFoundError("Downloaded files not found. Please check 'out_dir' and URLs.")


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2022-07-26/10300100D797E100-visual.tif
To: /content/maxar_tiles/10300100D797E100/031131233233.tif
100%|██████████| 52.3M/52.3M [00:01<00:00, 32.8MB/s]


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2023-02-08/10300500D9F8D200-visual.tif
To: /content/maxar_tiles/10300500D9F8D200/031131233233.tif
100%|██████████| 77.3M/77.3M [00:02<00:00, 26.7MB/s]


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2023-02-11/10300100E19A4400-visual.tif
To: /content/maxar_tiles/10300100E19A4400/031131233233.tif
100%|██████████| 51.0M/51.0M [00:02<00:00, 20.8MB/s]


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2023-02-11/10300100E291D100-visual.tif
To: /content/maxar_tiles/10300100E291D100/031131233233.tif
100%|██████████| 71.2M/71.2M [00:02<00:00, 29.6MB/s]


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Kahramanmaras-turkey-earthquake-23/ard/37/031131233233/2023-02-28/10300100E3154100-visual.tif
To: /content/maxar_tiles/10300100E3154100/031131233233.tif
100%|██████████| 77.4M/77.4M [00:03<00:00, 24.9MB/s]

Local pre-event path: maxar_tiles/10300100D797E100/031131233233.tif
Local post-event path: maxar_tiles/10300500D9F8D200/031131233233.tif


### Cell 6 – Compute a simple “change image” (clean rewrite)

This cell:

- Reads band 1 from pre and post images.
- Resamples the post image to match the pre image grid.
- Computes `diff = |post - pre|`.
- Writes a new GeoTIFF `diff_pre_post.tif` using a **clean, simple profile**
  (one band, float32, no special compression tricks).

We also delete any old `diff_pre_post.tif` file first to avoid corrupted leftovers.


In [ ]:
import os
import numpy as np
import rasterio
from rasterio.warp import reproject, Resampling

diff_path = "diff_pre_post.tif"

# 🔧 Remove any old/corrupted file first
if os.path.exists(diff_path):
    os.remove(diff_path)

with rasterio.open(pre_path) as src_pre, rasterio.open(post_path) as src_post:
    # Read band 1 as a simple brightness channel
    pre_band = src_pre.read(1).astype("float32")
    post_band = src_post.read(1).astype("float32")

    # Prepare an array with the same shape as pre-band for the resampled post-band
    dst_post = np.empty_like(pre_band, dtype="float32")

    # Reproject/resample post to the pre grid (same resolution, CRS, transform)
    reproject(
        source=post_band,
        destination=dst_post,
        src_transform=src_post.transform,
        src_crs=src_post.crs,
        dst_transform=src_pre.transform,
        dst_crs=src_pre.crs,
        resampling=Resampling.bilinear,
    )

    # Absolute difference as simple "change" measure
    diff = np.abs(dst_post - pre_band)

    # ✅ Build a fresh, clean profile for the output
    profile = {
        "driver": "GTiff",
        "height": diff.shape[0],
        "width": diff.shape[1],
        "count": 1,
        "dtype": "float32",
        "crs": src_pre.crs,
        "transform": src_pre.transform,
        "compress": "LZW",   # optional; you can remove this line if needed
    }

    # Write the difference image
    with rasterio.open(diff_path, "w", **profile) as dst_diff:
        dst_diff.write(diff, 1)

print("Saved difference raster to:", diff_path)


Saved difference raster to: diff_pre_post.tif


In [ ]:
!pip install osmnx

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.5/101.5 kB 6.2 MB/s eta 0:00:00


### Cell 7 – Get building footprints in the AOI (from OpenStreetMap with OSMnx)

This cell uses **OSMnx** directly to download building footprints from OpenStreetMap
within your AOI:

- Our `bbox` is `[min_lon, min_lat, max_lon, max_lat]` (west, south, east, north).
- OSMnx’s `features_from_bbox` expects a single tuple `(left, bottom, right, top)`.
- We then keep only polygon geometries and add a simple numeric `bld_id` for each building.

Note: if you get 0 buildings, the AOI might be very small or OSM might have sparse data there.
Try a slightly larger box.


In [ ]:
import numpy as np

# Make sure osmnx is available
try:
    import osmnx as ox
except ImportError:
    %pip install -q osmnx
    import osmnx as ox

# Our bbox is [min_lon, min_lat, max_lon, max_lat] = [left, bottom, right, top]
left, bottom, right, top = bbox

# Download OSM features (buildings) within the bounding box
buildings = ox.features.features_from_bbox(
    bbox=(left, bottom, right, top),
    tags={"building": True},
)

print("OSM features returned:", len(buildings))

# Drop empty geometries
buildings = buildings[~buildings.geometry.isna()].copy()

# Keep only polygon-like geometries (buildings as areas)
buildings = buildings[buildings.geom_type.isin(["Polygon", "MultiPolygon"])].copy()
print("Polygon buildings:", len(buildings))

# Ensure we are in lat/lon CRS
buildings = buildings.to_crs("EPSG:4326")

# Add a simple building ID
buildings["bld_id"] = np.arange(len(buildings)) + 1

buildings_gdf = buildings

buildings_gdf.head()


OSM features returned: 389
Polygon buildings: 389


geometry building  \
element id                                                                      
way     325100020  POLYGON ((36.92272 37.57381, 36.92322 37.57477...     roof   
        378424595  POLYGON ((36.9224 37.57701, 36.92245 37.57681,...   mosque   
        472863209  POLYGON ((36.91973 37.57284, 36.91971 37.57263...      yes   
        593019070  POLYGON ((36.92187 37.57307, 36.92199 37.57331...      yes   
        596067917  POLYGON ((36.92118 37.57338, 36.92072 37.5734,...      yes   

                  layer                 name           amenity religion  \
element id                                                                
way     325100020     1        Kapalı tribün               NaN      NaN   
        378424595   NaN  Mehmet Kirişçi Cami  place_of_worship   muslim   
        472863209   NaN                  NaN               NaN      NaN   
        593019070   NaN                  NaN               NaN      NaN   
        596067917   NaN      Gençlik Merkezi  community_centre      NaN   

                         leisure         source     sport landuse military  \
element id                                                                   
way     325100020            NaN            NaN       NaN     NaN      NaN   
        378424595            NaN            NaN       NaN     NaN      NaN   
        472863209            NaN            NaN       NaN     NaN      NaN   
        593019070  sports_centre  maxar Premium  swimming     NaN      NaN   
        596067917            NaN            NaN       NaN     NaN      NaN   

                  office addr:district check_date fixme healthcare note phone  \
element id                                                                      
way     325100020    NaN           NaN        NaN   NaN        NaN  NaN   NaN   
        378424595    NaN           NaN        NaN   NaN        NaN  NaN   NaN   
        472863209    NaN           NaN        NaN   NaN        NaN  NaN   NaN   
        593019070    NaN           NaN        NaN   NaN        NaN  NaN   NaN   
        596067917    NaN           NaN        NaN   NaN        NaN  NaN   NaN   

                   bld_id  
element id                 
way     325100020       1  
        378424595       2  
        472863209       3  
        593019070       4  
        596067917       5

### Cell 8 – Summarize brightness change per building (zonal statistics)

This cell:

- Uses `leafmap.zonal_stats` to compute the **mean change value** inside each building polygon from `diff_pre_post.tif`. :contentReference[oaicite:3]{index=3}  
- Stores the result in a new GeoDataFrame with a `mean_change` column.
- Creates a simple **damage class**:
  - `low`   – small change
  - `medium`
  - `high`  – large change

We use quantiles (33% and 66%) as rough thresholds for this demo.


In [ ]:
# Compute zonal statistics (mean of diff raster per building)
stats_gdf = leafmap.zonal_stats(
    buildings_gdf,
    diff_path,
    stats=["mean"],
    gdf_out=True
)

stats_gdf = stats_gdf.rename(columns={"mean": "mean_change"})
stats_gdf["mean_change"] = stats_gdf["mean_change"].fillna(0.0)

# Define simple thresholds based on quantiles
q1 = stats_gdf["mean_change"].quantile(0.33)
q2 = stats_gdf["mean_change"].quantile(0.66)

def classify_damage(x):
    if x < q1:
        return "low"
    elif x < q2:
        return "medium"
    else:
        return "high"

stats_gdf["damage_class"] = stats_gdf["mean_change"].apply(classify_damage)

stats_gdf[["bld_id", "mean_change", "damage_class"]].head()


bld_id  mean_change damage_class
0       1   128.992832         high
1       2    64.075955          low
2       3   138.238406         high
3       4    93.729316       medium
4       5    85.703474       medium

In [ ]:
!pip install localtileserver

### Cell 9 – Visualize per-building “damage” on an interactive map

This cell:

- Creates a new map centered on your AOI.
- Adds the **post-event tile** as background (visual check).
- Adds building polygons colored by `damage_class`:
  - **green**  = low change  
  - **orange** = medium  
  - **red**    = high  

Click on buildings to see their attributes.  
Remember: this is a **toy damage indicator**, *not* an official or validated product.


In [ ]:
# Simple style function for buildings
def style_function(feature):
    dmg = feature["properties"].get("damage_class", "low")
    if dmg == "high":
        color = "red"
    elif dmg == "medium":
        color = "orange"
    else:
        color = "green"
    return {
        "color": color,
        "fillColor": color,
        "fillOpacity": 0.4,
        "weight": 1,
    }

# Center of AOI
center_lat = (bbox[1] + bbox[3]) / 2
center_lon = (bbox[0] + bbox[2]) / 2

m_damage = leafmap_map.Map(center=(center_lat, center_lon), zoom=15)
m_damage.add_basemap("SATELLITE")

# Add post-event image as a COG layer if you like (optional, simple overlay)
# Note: post_path is a local GeoTIFF; leafmap.add_raster supports this.
m_damage.add_raster(post_path, layer_name="Post-event image", opacity=0.8)

# Add buildings colored by damage class
m_damage.add_gdf(
    stats_gdf,
    layer_name="Buildings – change-based damage (toy)",
    style_callback=style_function,
    info_mode="on_click"
)

m_damage


### Cell 10 – Visual “before vs after” slider (pre vs post)

This cell creates an interactive slider to compare the **pre-event** and **post-event**
images for the same AOI. Drag the vertical bar left/right to see the changes.


In [ ]:
leafmap.image_comparison(
    pre_path,
    post_path,
    label1="Pre-event",
    label2="Post-event",
)


### Cell 11 – Visual “post vs change” slider (optional)

This cell compares the **post-event image** with the **difference raster** (change map).
It helps you visually link bright change areas to actual damaged blocks.


In [ ]:
leafmap.image_comparison(
    post_path,
    diff_path,
    label1="Post-event",
    label2="Change (|post - pre|)",
)
